## HotChili Analytics trading notebook template
#### Configure by setting ALGO_NAME in cell below.
#### Run various options (backtest, ingest, live) by uncommenting one cell 

In [1]:
%matplotlib inline
%load_ext zipline

# %reload_ext zipline # Uncomment and use this when already loaded zipline extension for magic cell usage.

/home/hca-r2-001/miniconda3/envs/hca/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
/home/hca-r2-001/miniconda3/envs/hca/lib/python3.6/site-packages/odo/backends/pandas.py:94: FutureWarning: pandas.tslib is deprecated and will be removed in a future version.
You can access NaTType as type(pandas.NaT)
  @convert.register((pd.Timestamp, pd.Timedelta), (pd.tslib.NaTType, type(None)))


In [2]:
import pandas as pd

# Options you can uncomment and set:

# pd.set_option("max_colwidth", 300)
# pd.set_option("display.max_rows", 300)
# pd.set_option("display.max_columns", 50)
# pd.set_option('precision', 2)
# pd.options.display.float_format = '{:20,.2f}'.format

In [3]:
import os

hca_root_path = os.environ['HCA_ROOT']
print(f"hca_root_path = {hca_root_path}")

hca_root_path = /home/hca-ws2004/hca


# Construct algorithm strategy path names

Assumptions:

- the strategy is in a directory with the same name as the strategy in `ALGO_NAME` below
- the strategy is located in the hca-resources directory, which is located relative to `hca_root_path`, found above

In [4]:
ALGO_NAME = "HCA_In_and_Out" # <--- Supply name here

Other variables are derived from `ALGO_NAME`:

In [5]:
HCA_RESOURCES_PATH = hca_root_path + "/hca-resources/" 
ALGO_PATH          = HCA_RESOURCES_PATH + ALGO_NAME + "/" 
ALGO_BT            = ALGO_PATH + ALGO_NAME + ".py"
ALGO_BT_OUT        = ALGO_PATH + ALGO_NAME + ".pkl"
ALGO_LIVE          = ALGO_PATH + ALGO_NAME + "_Live-gld-lb95" + ".py"

print(f"""
ALGO_NAME          = {ALGO_NAME}
HCA_RESOURCES_PATH = {HCA_RESOURCES_PATH}
ALGO_PATH          = {ALGO_PATH}
ALGO_BT            = {ALGO_BT}
ALGO_BT_OUT        = {ALGO_BT_OUT}
ALGO_LIVE          = {ALGO_LIVE}

Contents of algo directory:
""")

!ls $ALGO_PATH


ALGO_NAME          = HCA_In_and_Out
HCA_RESOURCES_PATH = /home/hca-ws2004/hca/hca-resources/
ALGO_PATH          = /home/hca-ws2004/hca/hca-resources/HCA_In_and_Out/
ALGO_BT            = /home/hca-ws2004/hca/hca-resources/HCA_In_and_Out/HCA_In_and_Out.py
ALGO_BT_OUT        = /home/hca-ws2004/hca/hca-resources/HCA_In_and_Out/HCA_In_and_Out.pkl
ALGO_LIVE          = /home/hca-ws2004/hca/hca-resources/HCA_In_and_Out/HCA_In_and_Out_Live-gld-lb95.py

Contents of algo directory:

HCA_In_and_Out_bt.pkl		       in_and_out_live_state-2021-07-17.txt
HCA_In_and_Out.ipynb		       in_and_out_live_state-Copy1.txt
HCA_In_and_Out_Live-gld-lb95.py        in_and_out_live_state.csv
HCA_In_and_Out_Live-IRA.py	       in_and_out_live_state-IRA.txt
HCA_In_and_Out_Live.py		       in_and_out_state.txt
HCA_In_and_Out.pkl		       Q_In_and_Out_orig.py
HCA_In_and_Out.py		       realtime-bars
HCA_In_and_Out_Q.py		       strategy.state
HCA_In_and_Out_tearsheet(3).html       strategy-U2822754.state
HCA_In_and_Out_tear

## Zipline backtest: 

- Method: Jupyter magic cell (%%) 
- Execution of zipline code in cell containing command line command
- Uncomment first line and hit (shift-enter) inside the cell to run simulation backtest

%%zipline --start=2020-1-1 --end=2021-7-16 -b sharadar-funds -o $ALGO_BT_OUT

# Vlad Code from: Aleksei Dremov  in
# https://www.quantopian.com/posts/live-slash-paper-trade-the-in-out-stragegy

# Price relative ratios (intersection) with wait days
import numpy as np

from zipline.api import order, cancel_order, get_open_orders, symbol, symbols, date_rules, time_rules, order_target_percent, record, schedule_function, get_datetime
from trading_calendars import get_calendar

def initialize(context):
    # -----------------------------------------------------------------------------------------------
    # YAHOO_SYM_LST=QQQ,TLT,IEF,SLV,GLD,XLI,XLU zipline ingest -b yahoo_direct
    c = context
    #orig c.STOCKS = symbols('QQQ'); c.BONDS = symbols('TLT','IEF'); c.LEV = 1.00; c.wt = {};
    #ajjc
    c.STOCKS = symbols('QQQ', 'IWB'); c.BONDS = symbols('IEF','GLD'); c.LEV = 1.00; c.wt = {};
    #c.STOCKS = symbols('QQQ', 'URTH'); c.BONDS = symbols('TLT','IEF','SCHD'); c.LEV = 1.00; c.wt = {};
    c.A = symbol('SLV'); c.B = symbol('GLD'); c.C = symbol('XLI'); c.D = symbol('XLU');
    c.MKT = symbol('QQQ'); c.VOLA = 126; c.LB = 0.95; c.BULL = 1; c.COUNT = 0; c.OUT_DAY = 0; c.RET_INITIAL = 80;
# -----------------------------------------------------------------------------------------------

    # schedule_function(daily_check, date_rules.every_day(), time_rules.market_open(minutes = 140))
    # schedule_function(record_vars, date_rules.every_day(), time_rules.market_close())
    
def minut(context): #Minute of trading day
    dt = context.get_datetime().astimezone(pytz.timezone('US/Eastern'))
    return (dt.hour * 60) + dt.minute - 570
            
#def handle_data(context, data):
#    time_now = minut(context)
#    log.info("___handle_data: {} = Current Trading Minute".format(time_now))
     
def handle_data(context, data):
    if (not context.ORDERS_DONE):
        context.ORDERS_DONE = True
        daily_check(context,data) #Name of the original algo trading function
        trade(context,data,context.wt)
        record_vars(context, data)        
    else:
        print("Exiting: zipline-broker: context.portfolio : {}".format(context.portfolio))
        exit()
        
def before_trading_start(context, data):
    c = context
    c.ORDERS_DONE       = False #No Orders done yet today
    c.all_orders = {} 
# End:Zipline Builtin Functions
        

def daily_check(context,data):
    c = context
    #global c.BULL, c.COUNT, OUT_DAY
    vola = data.history(c.MKT, 'price',  c.VOLA + 1, '1d').pct_change().std() * np.sqrt(252)
    WAIT_DAYS = int(vola * c.RET_INITIAL)
    RET = int((1.0 - vola) * c.RET_INITIAL)
    P = data.history([c.A,c.B,c.C,c.D], 'price',  RET + 2, '1d').iloc[:-1].dropna()
    ratio_ab = (P[c.A].iloc[-1] / P[c.A].iloc[0]) / (P[c.B].iloc[-1] / P[c.B].iloc[0])
    ratio_cd = (P[c.C].iloc[-1] / P[c.C].iloc[0]) / (P[c.D].iloc[-1] / P[c.D].iloc[0])
    exit = ratio_ab < c.LB and ratio_cd < c.LB
    if exit: c.BULL = 0; c.OUT_DAY = c.COUNT;
    elif (c.COUNT >= c.OUT_DAY + WAIT_DAYS): c.BULL = 1
    c.COUNT += 1
    wt_stk = c.LEV if c.BULL else 0;
    wt_bnd = 0 if c.BULL else c.LEV;
    for sec in c.STOCKS: c.wt[sec] = wt_stk / len(c.STOCKS);
    for sec in c.BONDS: c.wt[sec] = wt_bnd / len(c.BONDS)
    
    print("WAIT_DAYS={} RET={} exit={} c.COUNT={} c.BULL={} c.OUT_DAY={}".format(WAIT_DAYS,RET,exit,c.COUNT,c.BULL,c.OUT_DAY))
    print("Trading Weights Today: wt_stk={} wt_bnd={} wts={}".format(c.wt,wt_stk,wt_bnd))
    
    #for sec, weight in c.wt.items():
        #order_target_percent(sec, weight)
    #record( wt_bnd = wt_bnd, wt_stk = wt_stk )

def trade(context,data,wts):
    lev = context.LEV #Should allow for a small percentage of Cash, to enable ordering fluctuations without having order cancelled.
    
    ### ajjc: Find a way to return if already traded today
    
    #print("TradingLinkData: Zipline-broker: context.portfolio : {}".format(context.portfolio))
    #print("TradingLinkData: IB-Account    : context.account   : {}".format(context.account))
    
    #acct_liq    = context.portfolio.starting_cash #Same as IB net_liquidation when measured daily
    acct_liq    = context.portfolio.portfolio_value #Same as IB net_liquidation
    acct_invest = lev * acct_liq   
    positions      = context.portfolio.positions
    #Live positions      = context.broker.positions
    
    # Get rid of positions not in wts
    for key in positions:
        if (key not in wts and not get_open_orders(key)):
            order(key, -positions[key].amount)      
        
    for stk,weight in wts.items():
        if data.can_trade(stk) and not get_open_orders(stk):
            if stk in positions:
                current_amt = positions[stk].amount
                rebalance_amt = int(acct_invest*(weight) / data.current(stk,'price'))
                delta_amt = rebalance_amt - current_amt
                if delta_amt != 0:
                    order(stk, delta_amt) 
                else:
                    print("No new orders for : {}".format(stk))

            if (stk not in positions and data.can_trade(stk) 
                and not get_open_orders(stk)):
                
                amt = int(acct_invest*(weight) / data.current(stk,'price'))
                order(stk, amt)                                                    

def record_vars(context, data):
    record(leverage = context.account.leverage)

## Display your current bundles

In [6]:
#!zipline bundles # Finds all bundles

## Ingest Sharadar funds assets for today

In [7]:
# Ingest Sharadar funds assets for today, if needed.

# Only need to ingest Funds for this algo, and this takes less processing time and system memory than ingesting
# all of Sharadar Equities plus Funds bundle (sharadar-eqfd)
# !zipline ingest -b sharadar-funds

## Zipline backtest, alternative method

- Method: command line
- Execution of zipline code, located in a file, using below command line execution with magic (`!`) invocation
- This line can also be run in a terminal by copying everything past the `!` and pasting (shift-insert) it into the target terminal

In [8]:
!zipline run -f $ALGO_LIVE  --start=2019-1-1 --end=2021-07-16 --capital-base 100000 -b sharadar-funds -o $ALGO_BT_OUT

/home/hca-r2-001/miniconda3/envs/hca/lib/python3.6/site-packages/h5py/__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters
/home/hca-r2-001/miniconda3/envs/hca/lib/python3.6/site-packages/odo/backends/pandas.py:94: FutureWarning: pandas.tslib is deprecated and will be removed in a future version.
You can access NaTType as type(pandas.NaT)
  @convert.register((pd.Timestamp, pd.Timedelta), (pd.tslib.NaTType, type(None)))
extension: hca_root_path = /home/hca-ws2004/hca
extension:TODAY_STR = 2021-07-18
extension:TWO_YR_AGO_STR = 2019-07-18
extension:  start_date=2019-07-18 end_date = 2021-07-18
[2021-07-18 23:52:59.136245] WARNING: Loader: Refusing to download new benchmark data because a download succeeded at 2021-07-18 23:22:17.788943+00:00.
[2021-07-18 23:52:59.166697] WARNING: Loade

### Run Zipline live on IB-TWS via command line

- Method: command line
- Execution of zipline code using below command line execution using magic (`!`) invocation

**Notes:** 
- IB-TWS or IB-Gateway must be running, with `IB_ACCT` and `IB_URI` port being correct to live trade
- Change `I_WANT_TO_RUN_THIS_CODE` to `True` below to run zipline live on IB-TWS/IB-Gateway

In [9]:
TODAY = pd.datetime.today().strftime("%Y-%m-%d")
print("TODAY = {}".format(TODAY))

TODAY = 2021-07-18


In [10]:
ALGO_STATE = ALGO_PATH + "strategy.state" 
ALGO_RTB   = ALGO_PATH + "realtime-bars/"

# Edit the following URI to match your IB account and port info.
IB_ACCT = "DU1568488"
IB_URI = "127.0.0.1:7497:1301"

# Change following to 'True' and run cell (control-enter) to execute live run.
I_WANT_TO_RUN_THIS_CODE = False
#I_WANT_TO_RUN_THIS_CODE = True

if I_WANT_TO_RUN_THIS_CODE:
    
    !zipline run \
        -s $TODAY \
        -f $ALGO_LIVE \
        --bundle sharadar-funds \
        --broker ib \
        --broker-uri $IB_URI \
        --broker-acct $IB_ACCT \
        --data-frequency daily \
        --state-file $ALGO_STATE \
        --realtime-bar-target $ALGO_RTB 

In [ ]:
import os
#os.environ['ZIPLINE_ROOT'] = os.path.join(os.getcwd(), '.zipline')

os.listdir(os.environ['ZIPLINE_ROOT'])
import zipline
from zipline.data import bundles

bundle_name = 'sharadar-funds'
bundle_data = bundles.load(bundle_name)
from zipline.pipeline.loaders import USEquityPricingLoader
from zipline.utils.calendars import get_calendar
from zipline.pipeline.data import USEquityPricing
from zipline.data.data_portal import DataPortal

import pandas as pd

# Set the dataloader
pricing_loader = USEquityPricingLoader(bundle_data.equity_daily_bar_reader, bundle_data.adjustment_reader)
#new pricing_loader = USEquityPricingLoader.without_fx(bundle_data.equity_daily_bar_reader, bundle_data.adjustment_reader)


# Define the function for the get_loader parameter
def choose_loader(column):
    if column not in USEquityPricing.columns:
        raise Exception('Column not in USEquityPricing')
    return pricing_loader

# Set the trading calendar
trading_calendar = get_calendar('NYSE')

start_date = pd.Timestamp('2019-07-05', tz='utc')
end_date = pd.Timestamp('2020-11-13', tz='utc')

# Create a data portal
data_portal = DataPortal(bundle_data.asset_finder,
                         trading_calendar = trading_calendar,
                         first_trading_day = start_date,
                         equity_daily_reader = bundle_data.equity_daily_bar_reader,
                         adjustment_reader = bundle_data.adjustment_reader)

In [ ]:
from zipline.utils.calendars import get_calendar
from zipline.pipeline.data import USEquityPricing
from zipline.pipeline.engine import SimplePipelineEngine

# Create a Pipeline engine
engine = SimplePipelineEngine(get_loader = choose_loader,
                              asset_finder = bundle_data.asset_finder, calendar=trading_calendar.all_sessions)

In [37]:
#from zipline.pipeline.domain import US_EQUITIES
from zipline.pipeline.factors import AverageDollarVolume
from zipline.pipeline import Pipeline

# Create a screen for our Pipeline
universe = AverageDollarVolume(window_length = 5).top(10)

# Create an empty Pipeline with the given screen
pipeline = Pipeline(screen = universe)
#new pipeline = Pipeline(screen = universe, domain=US_EQUITIES)
pipeline.add(AverageDollarVolume(window_length = 5), "Dollar Volume")

In [38]:
# Set the start and end dates
start_date = pd.Timestamp('2020-10-29', tz = 'utc')
end_date = pd.Timestamp('2020-11-3', tz = 'utc')

# Run our pipeline for the given start and end dates
pipeline_output = engine.run_pipeline(pipeline, start_date, end_date)

pipeline_output.head()


Dollar Volume
2020-10-29 00:00:00+00:00 Equity(29 [AAPL])     1.200492e+10
                          Equity(631 [AMD])     6.096783e+09
                          Equity(715 [AMZN])    1.489481e+10
                          Equity(1296 [BABA])   3.123722e+09
                          Equity(4199 [FB])     5.220827e+09

In [23]:
def make_pipeline(): 
    mean_close_10 = SimpleMovingAverage(inputs=[USEquityPricing.close],window_length=10) 
    mean_close_30 = SimpleMovingAverage(inputs=[USEquityPricing.close],window_length=30) 
    
    latest_close = USEquityPricing.close.latest  
    
    perc_diff = (mean_close_10 - mean_close_30) / mean_close_30  
    
    return Pipeline(columns={ 'Percent Difference':perc_diff, '30 Day Mean Close':mean_close_30, 'Latest Close':latest_close })

ModuleNotFoundError: No module named 'zipline.pipeline.Pipeline'

In [14]:
results = run_pipeline(make_pipeline(),'2018-01-01','2019-01-01')

NameError: name 'run_pipeline' is not defined